# Lab 2: Unsupervised extraction of bilingual lexicon

In [ ]:
import math

from collections import Counter, defaultdict
from itertools import product, chain
from operator import itemgetter
from io import StringIO

# paths to the corpus
src = "french.corpus"
tgt = "english.corpus"

## Count word occurences

The goal is to count the number of sentences where each word appears in.
We need to be carefull if a word appears more than one time in a single sentence as this should still count for one occurence.

To keep keep track the number of occurences of each word, we will use a Counter: https://docs.python.org/3/library/collections.html#counter-objects
This object works similarly to a dictionnary where keys are object to be counted (i.e. words) and values are the number of occurences.

In [ ]:
counts = Counter()  # create a counter
counts["the"] += 1  # add one occurence for word "the"

# Add occurences for each word in the list
# Because "dog" appears twice, its number of occurences will be incremented twice
counts.update(["the", "dog", "is", "a", "dog"])

# Warning: strings are iterable, so the following line will not throw an error,
# but it won't add an occurence to word "an":
# it will increment the count of (single character) words "a" and "n"
counts.update("an")

# print the content
print(counts)

# most_common(k) returns the k most common words as a list of tuples,
# each tuple containing the word and its number of occurences
print(counts.most_common(2))

In the corpus, there is one sentence per line.
The sentence are tokenized, that is spaces are placed to separe tokens (e.g. adding space before all punctuations to seperate them from words).
Therefore, we iterate over the file stream to read each sentence at a time.
Then, line.split() will return the sequence of words in the sentence as a list of strings.

However, we cannot pass this list directly to the counter because we don't want to count twice a word appearing two times in a sentence.
A trick to do that is to convert the list into a set: https://docs.python.org/3/library/stdtypes.html#set-types-set-frozenset
A set is an unordered collection where each element only appears one, so duplicates will be removed.

In [ ]:
def count_sentences_with_word(instream):
    # TODO

In [ ]:
def test_count_sentences_with_word():
    # We can use a StringIO object to simulate reading from a file
    # without actually creating a temporary file for the tests
    input = StringIO("""a b c
d c a
""")
    assert count_sentences_with_word(input) == {'a': 2, 'c': 2, 'b': 1, 'd': 1}

test_count_sentences_with_word()

In [ ]:
# print the 10 most common words in the src file
with open(src) as ifile:
    src_counts = count_sentences_with_word(ifile)
    
# iterate over tuples in the list
for word, occurences in src_counts.most_common(10):
    print("Word \"%s\" appears in %i sentence(s)." % (word, occurences))

We can also write a more compact function to do the same thing in a single line of code. To do that, we use the chain.from_iterable function: https://docs.python.org/2/library/itertools.html#itertools.chain.from_iterable

**Warning:** if you don't understand how to do this, first finish all the lab exercise and then try to do it.

In [ ]:
def count_sentences_with_word(ifile):
    # TODO
    
test_count_sentences_with_word()

In [ ]:
with open(src) as ifile:
    src_counts = count_sentences_with_word(ifile)
    
# iterate over the tuples in the list
for word, occurences in src_counts.most_common(10):
    print("Word \"%s\" appears in %i sentence(s)." % (word, occurences))

## Build co-occurences tables

We need to build word co-occurences tables, i.e. count how many times each word the source corpus occurs with translation words in the target sentence. For example:

- Source: The dog is eating
- Target: Le chien mange

We need to count that "The" co-occurs with "Le", "chien" and "mange", and similarly for other word in the source sentence.
To loop over sentences of both files at the same time, you can use the python zip() function https://docs.python.org/3.3/library/functions.html#zip

In order to do that, we need a build a nested loop:

- loop over each word in the source sentence
- inside the first loop, loop over the target sentence words and increment co-occurences

Instead of this nested loop, we can use the product function provided in python: https://docs.python.org/3/library/itertools.html#itertools.product


In [ ]:
def build_cooc_table(src, tgt):
    # co-occurence counter
    # note that this time keys will be tuples (source word, target word)
    cooc_table = Counter()
    
    # TODO

    return cooc_table

In [ ]:
def test_build_cooc_table():

    src = StringIO(""" a b c a
d c a
""")
    tgt = StringIO("""A B C A
D C A
""")

    res = build_cooc_table(src, tgt)
    expected_res = {('c', 'C'): 2,
                    ('c', 'A'): 2,
                    ('a', 'C'): 2,
                    ('a', 'A'): 2,
                    ('c', 'B'): 1,
                    ('b', 'B'): 1,
                    ('b', 'C'): 1,
                    ('b', 'A'): 1,
                    ('a', 'B'): 1,
                    ('c', 'D'): 1,
                    ('a', 'D'): 1,
                    ('d', 'A'): 1,
                    ('d', 'D'): 1,
                    ('d', 'C'): 1}

    assert res == expected_res

test_build_cooc_table()

The coocurence table is a dictionnary where keys are tuple of words and values are likelihood ratios.
We can get the dictionnary content as an iterator over tuples of (key, value) with the items() method.
To find plausible translation, we need to sort the content with respect the values (i.e. number of coocurences), which can be achieved with the sorted() function https://docs.python.org/3/howto/sorting.html

- the first argument is the iterator to sort
- named argument key let us choose how to sort: we want to sort with respect to the ratio of each tuple (couple of words, likelihood ratio), so we can use itemgetter(1) as a key https://docs.python.org/3/library/operator.html#operator.itemgetter Equivalently, we could have used a lambda expression, i.e. key=lambda x: x[1]
- named argument reverse allow use to sort in decreasing order

In [ ]:
print("100 best unsupervised word translation:")

# TODO

# Likelihood ratio

We just need to implement the formula!

In [ ]:
def ll_ratio(n_a, n_b, n_ab, n):
    """
    For source word a and target word b:
    - n_a: number of occurences of a in source sentences
    - n_b: number of occurences of b of target sentences
    - n_ab: number of co-occurences of a and b in translated sentences
    - number of sentences
    """
    
    # pass

    return ll

We can now compute the ratio for all couple of words.

In [ ]:
def compute_ll_ratio(src, tgt, cooc_table, n_sentence):
    # src: counts of words in source sentences
    # tgt: counts of words in target sentences
    # cooc_table: co-occurences table
    # n_sentence: number of sentences

    ratios = {}
    # TODO
    # (warning, you may need to catch an exception to bypass problems here,
    # depending on how you code this function...)

    return ratios

## Build unsupervised translation dictionnary

In [ ]:
# Count number of sentences
# TODO

with open(src) as src_file, open(tgt) as tgt_file:
    src_counts = count_sentences_with_word(src_file)
    tgt_counts = count_sentences_with_word(tgt_file)

cooc = build_cooc_table(open(src), open(tgt))

ll_ratios = compute_ll_ratio(src_counts, tgt_counts, cooc, n_sentence)

In [ ]:
# The ratio is a dictionnary where keys are tuple of words and values are likelihood ratios.
# so we can do the same thing as previously to get the best translations
print("100 best unsupervised word translation with likelihood ratio:")
# TODO